In [8]:
from langchain_community.document_loaders import TextLoader
from langchain_text_splitters             import CharacterTextSplitter
from langchain_huggingface                import HuggingFaceEmbeddings
from langchain_chroma                     import Chroma

In [9]:
import pandas as pd

books = pd.read_csv('./data/books_cleaned.csv')
books.head()

isbn13             full_title                          authors  \
0  9780002005883                 Gilead               Marilynne Robinson   
1  9780002261982  Spider's Web: A Novel  Charles Osborne;Agatha Christie   
2  9780006178736         Rage of angels                   Sidney Sheldon   
3  9780006280897         The Four Loves              Clive Staples Lewis   
4  9780006280934    The Problem of Pain              Clive Staples Lewis   

                      categories  \
0                        Fiction   
1  Detective and mystery stories   
2                        Fiction   
3                 Christian life   
4                 Christian life   

                                         description  \
0  A NOVEL THAT READERS and critics have been eag...   
1  A new 'Christie for Christmas' -- a full-lengt...   
2  A memorable, mesmerizing heroine Jennifer -- b...   
3  Lewis' work on the nature of love divides love...   
4  "In The Problem of Pain, C.S. Lewis, one of th...   

                                           full_desc  published_year  \
0  9780002005883 A NOVEL THAT READERS and critics...          2004.0   
1  9780002261982 A new 'Christie for Christmas' -...          2000.0   
2  9780006178736 A memorable, mesmerizing heroine...          1993.0   
3  9780006280897 Lewis' work on the nature of lov...          2002.0   
4  9780006280934 "In The Problem of Pain, C.S. Le...          2002.0   

   num_pages  average_rating  ratings_count  \
0      247.0            3.85          361.0   
1      241.0            3.83         5164.0   
2      512.0            3.93        29532.0   
3      170.0            4.15        33684.0   
4      176.0            4.09        37569.0   

                                           thumbnail  
0  http://books.google.com/books/content?id=KQZCP...  
1  http://books.google.com/books/content?id=gA5GP...  
2  http://books.google.com/books/content?id=FKo2T...  
3  http://books.google.com/books/content?id=XhQ5X...  
4  http://books.google.com/books/content?id=Kk-uV...

In [10]:
# Change data to type that TextLoader can handle
books['full_desc'].to_csv('data/full_desc.txt', sep='\n',
                                   index=False, header=False)

In [11]:
# Split data into documents
raw_docs      = TextLoader('./data/full_desc.txt').load()
text_splitter = CharacterTextSplitter(chunk_size=0, chunk_overlap=0, separator='\n')
docs          = text_splitter.split_documents(raw_docs)

Created a chunk of size 1168, which is longer than the specified 0
Created a chunk of size 1214, which is longer than the specified 0
Created a chunk of size 373, which is longer than the specified 0
Created a chunk of size 309, which is longer than the specified 0
Created a chunk of size 483, which is longer than the specified 0
Created a chunk of size 482, which is longer than the specified 0
Created a chunk of size 960, which is longer than the specified 0
Created a chunk of size 188, which is longer than the specified 0
Created a chunk of size 843, which is longer than the specified 0
Created a chunk of size 296, which is longer than the specified 0
Created a chunk of size 197, which is longer than the specified 0
Created a chunk of size 881, which is longer than the specified 0
Created a chunk of size 1088, which is longer than the specified 0
Created a chunk of size 1189, which is longer than the specified 0
Created a chunk of size 304, which is longer than the specified 0
Create

In [12]:
# Embedding and Save to database
huggingface_embeddings = HuggingFaceEmbeddings(
    model_name='sentence-transformers/all-MiniLM-L6-v2',
    model_kwargs={'device': 'cuda'}
)

db_books = Chroma.from_documents(
    documents=docs,
    embedding=huggingface_embeddings
)

In [13]:
def retrieval(query: str, top_k: int=10) -> pd.DataFrame:
    docs = db_books.similarity_search(query, k=50)

    books_list = []
    for i in range(len(docs)):
        books_list += [int(docs[i].page_content.strip('"').split()[0])]

    return books[books['isbn13'].isin(books_list)].head(top_k)

retrieval('A book to teach children about nature')

isbn13                                         full_title  \
59    9780007151240                                     The Family Way   
404   9780064402453                         Racso and the Rats of NIMH   
406   9780064403870                R-T, Margaret, and the Rats of NIMH   
407   9780064404419                                 The Rainbow People   
416   9780064406925                                 Winter on the Farm   
429   9780064434980                               The Deer in the Wood   
991   9780192862099  The Origins of Life: From the Birth of Life to...   
1078  9780241003008                        The Very Hungry Caterpillar   
1639  9780374422080                             Everything on a Waffle   
1642  9780374522599                              The Control of Nature   

                                authors         categories  \
59                         Tony Parsons         Parenthood   
404                   Jane Leslie Conly   Juvenile Fiction   
406                   Jane Leslie Conly   Juvenile Fiction   
407                        Laurence Yep   Juvenile Fiction   
416                Laura Ingalls Wilder   Juvenile Fiction   
429                Laura Ingalls Wilder   Juvenile Fiction   
991   John Maynard Smith;Eörs Szathmáry            Science   
1078                         Eric Carle  Babytime resource   
1639                      Polly Horvath   Juvenile Fiction   
1642                        John McPhee             Nature   

                                            description  \
59    It should be the most natural thing in the wor...   
404   ‘Racso, a brash and boastful little rodent, is...   
406   When Margaret and her younger brother, Artie, ...   
407   "Culled from 69 stories collected in a [1930s]...   
416   The Little House books tell the story of a lit...   
429   Even the youngest child can enjoy a special ad...   
991   'I can recommend this book as a thoroughly int...   
1078  Eric Carle's children's classic is the story o...   
1639  This Newbery Honor Book tells the story of 11 ...   
1642  The Control of Nature is John McPhee's bestsel...   

                                              full_desc  published_year  \
59    9780007151240 It should be the most natural th...          2005.0   
404   9780064402453 ‘Racso, a brash and boastful lit...          1988.0   
406   9780064403870 When Margaret and her younger br...          1991.0   
407   9780064404419 "Culled from 69 stories collecte...          1992.0   
416   9780064406925 The Little House books tell the ...          1997.0   
429   9780064434980 Even the youngest child can enjo...          1999.0   
991   9780192862099 'I can recommend this book as a ...          2000.0   
1078  9780241003008 Eric Carle's children's classic ...          1994.0   
1639  9780374422080 This Newbery Honor Book tells th...          2004.0   
1642  9780374522599 The Control of Nature is John Mc...          1990.0   

      num_pages  average_rating  ratings_count  \
59        400.0            3.51         2095.0   
404       288.0            3.76         3231.0   
406       272.0            3.52          631.0   
407       208.0            3.75          202.0   
416        32.0            4.13          400.0   
429        32.0            4.17          302.0   
991       192.0            4.11           41.0   
1078       26.0            4.29       340101.0   
1639      150.0            3.71         9631.0   
1642      288.0            4.24         3365.0   

                                              thumbnail  
59    http://books.google.com/books/content?id=dJEIx...  
404   http://books.google.com/books/content?id=MgoNv...  
406   http://books.google.com/books/content?id=WTHHH...  
407   http://books.google.com/books/content?id=5AHwq...  
416   http://books.google.com/books/content?id=IvlKH...  
429   http://books.google.com/books/content?id=V7YDW...  
991   http://books.google.com/books/content?id=nHDbB...  
1078  http://books.googl